## Setup

In [ ]:
from IPython import get_ipython
ipython = get_ipython()
ipython.run_line_magic("load_ext", "autoreload")
ipython.run_line_magic("autoreload", "2")

import os
import sys
import torch as t
import einops
from pathlib import Path
import circuitsvis as cv
from IPython.display import display
from transformer_lens import HookedTransformer
from eindex import eindex
from rich import print as rprint
from rich.table import Table
import string

# Make sure exercises are in the path
chapter = r"chapter1_transformer_interp"
exercises_dir = Path(f"{os.getcwd().split(chapter)[0]}/{chapter}/exercises").resolve()
section_dir = exercises_dir / "monthly_algorithmic_problems" / "january24_caesar_cipher"
if str(exercises_dir) not in sys.path: sys.path.append(str(exercises_dir))

from monthly_algorithmic_problems.january24_caesar_cipher.training import train, TrainArgs
from monthly_algorithmic_problems.january24_caesar_cipher.dataset import CodeBreakingDataset
from plotly_utils import imshow

device = t.device("cuda" if t.cuda.is_available() else "cpu")

MAIN = __name__ == "__main__"

## Dataset

This problem has 3 modes of difficulty, corresponding to 3 different datasets.

* In "easy mode", the dataset only contains 3-letter words which are among the 100 most common in the English language (as approximated by their frequency in Hitchhiker's Guide To The Galaxy). The dataset is stored in `data/hitchhikers.txt`. The tokens are single letters and space (so we have 27 tokens in total).
* In "medium mode", it's the same as easy mode, except that the words are chosen from these top 100 3-letter words uniformly, rather than by their frequency in the book.
* In "hard mode", it's actual natural language text - although we've made it easier by making everything lowercase and removing punctuation except for `.,:;?!"'` (as well as space and newline), meaning the size of the vocabulary is 26 + 10 = 36. The data is taken from OpenWebText.

You can see `dataset.py` for more details.

Before each model training, we'll show you a demo of the dataset for that particular mode.

# Code to visualise a model's output

This is a convenience function, which does the following:

* Prints stats summarizing model performance on a dataset of size 1000
* Visualises the attention patterns on a bunch of inputs (by default the first 10 in the batch)
* Plots the logits for a particular example in the dataset (by default the first in the batch)

This is run at the end of each model's training. It's designed to help you get started with interp.

In [ ]:
def show(model: HookedTransformer, batch_idx: int, mode="easy", n=10):

    kwargs = dict(word_list_size=100, path="hitchhikers.txt", seq_len=32) if mode != "hard" else dict(seq_len=32)
    dataset = CodeBreakingDataset(mode=mode, size=500, **kwargs).to(device)

    batch_size, seq_len = dataset.toks.shape

    logits, cache = model.run_with_cache(dataset.toks)

    logprobs = logits.log_softmax(-1) # [batch seq_len vocab_out]
    probs = logprobs.softmax(-1) # [batch seq_len vocab_out]

    # We want to index like `logprobs_correct[batch, seq] = logprobs[batch, seq, labels[batch]]`
    logprobs_correct = eindex(logprobs, dataset.labels, "batch seq [batch]")
    probs_correct = eindex(probs, dataset.labels, "batch seq [batch]")

    print(f"Average cross entropy loss: {-logprobs_correct.mean().item():.3f}")
    print(f"Mean probability on correct label: {probs_correct.mean():.3f}")
    print(f"Median probability on correct label: {probs_correct.median():.3f}")
    print(f"Min probability on correct label: {probs_correct.min():.3f}")

    cv.attention.from_cache(
        cache = cache,
        tokens = dataset.str_toks,
        batch_idx = list(range(n)),
        radioitems = True,
        return_mode = "view",
        batch_labels = ["".join(s) + "  ====  " + "".join(s2) for s, s2 in zip(dataset.str_toks[:n], dataset.str_toks_raw[:n])],
        mode = "small",
    )

    logits = model(dataset.toks[batch_idx].unsqueeze(0)).squeeze() # [seq_len vocab_out]
    probs = logits.softmax(dim=-1) # [seq_len vocab_out]

    imshow(
        probs.T,
        y=dataset.vocab_out,
        x=[f"{s}<br><sub>({j})</sub>" for j, s in enumerate(dataset.str_toks[batch_idx])],
        labels={"x": "Token", "y": "Vocab"},
        xaxis_tickangle=0,
        title=f"Sample model probabilities:<br>{''.join(dataset.str_toks[batch_idx])}",
        text=[
            ["〇" if (s == dataset.str_labels[batch_idx]) else "" for _ in range(seq_len)]
            for s in dataset.vocab_out
        ],
        width=750,
        height=600,
    )

## Transformer (easy)

### Demo of dataset in easy mode

In [ ]:
data = CodeBreakingDataset(mode="easy", size=5, word_list_size=100, seq_len=30, path="hitchhikers.txt")

table = Table("Pre-encoding", "Post-encoding", "Rotation", title="Easy mode")
for i in range(5):
    rotation = int(data.str_labels[i])
    rotation_explained = f"{rotation:02}: a -> {string.ascii_lowercase[rotation % 26]}, b -> {string.ascii_lowercase[(rotation + 1) % 26]}, ..."
    table.add_row(
        "".join(data.str_toks_raw[i]),
        "".join(data.str_toks[i]),
        rotation_explained,
    )
rprint(table)

                                        Easy mode                                        
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Pre-encoding                 ┃ Post-encoding                ┃ Rotation                ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ who and the not you was for  │ ozg sfv lzw fgl qgm osk xgj  │ 18: a -> s, b -> t, ... │
│ the you but the for the for  │ ocz tjp wpo ocz ajm ocz ajm  │ 21: a -> v, b -> w, ... │
│ but was the are own his the  │ haz cgy znk gxk uct noy znk  │ 06: a -> g, b -> h, ... │
│ one his was and but put the  │ sri lmw aew erh fyx tyx xli  │ 04: a -> e, b -> f, ... │
│ the had the had for and out  │ xli leh xli leh jsv erh syx  │ 04: a -> e, b -> f, ... │
└──────────────────────────────┴──────────────────────────────┴─────────────────────────┘

### Training model

In [ ]:
args = TrainArgs(

    # Training arguments
    trainset_size=150_000,
    valset_size=10_000,
    epochs=100,
    batch_size=512,
    lr_start=1e-3,
    lr_end=1e-4,
    weight_decay=0.001,
    seed=42,
    use_wandb=False,
    device=device,

    # Model architecture arguments
    d_model=48,
    d_head=24,
    n_layers=2,
    n_heads=2,
    d_mlp=None,
    normalization_type="LN",
    
    # Dataset arguments
    mode="easy",
    word_list_size=100,
    seq_len=32,
    path="hitchhikers.txt",
)

# Train the model
model = train(args)

# Save the model
filename = section_dir / "code_breaking_model_easy.pt"
t.save(model.state_dict(), filename)

Building dataset...:   0%|          | 0/150000 [00:00<?, ?it/s]

Epoch 00, Train loss = 0.3835, Accuracy: 0.9093, LR = 9.91e-04
Epoch 01, Train loss = 0.2565, Accuracy: 0.9355, LR = 9.82e-04
Epoch 02, Train loss = 0.2083, Accuracy: 0.9462, LR = 9.73e-04
Epoch 03, Train loss = 0.1917, Accuracy: 0.9503, LR = 9.64e-04
Epoch 04, Train loss = 0.1534, Accuracy: 0.9540, LR = 9.55e-04
Epoch 05, Train loss = 0.1567, Accuracy: 0.9564, LR = 9.46e-04
Epoch 06, Train loss = 0.1593, Accuracy: 0.9570, LR = 9.37e-04
Epoch 07, Train loss = 0.1603, Accuracy: 0.9575, LR = 9.28e-04
Epoch 08, Train loss = 0.1578, Accuracy: 0.9583, LR = 9.19e-04
Epoch 09, Train loss = 0.1457, Accuracy: 0.9587, LR = 9.10e-04
Epoch 10, Train loss = 0.1416, Accuracy: 0.9595, LR = 9.01e-04
Epoch 11, Train loss = 0.1303, Accuracy: 0.9603, LR = 8.92e-04
Epoch 12, Train loss = 0.1468, Accuracy: 0.9609, LR = 8.83e-04
Epoch 13, Train loss = 0.1417, Accuracy: 0.9608, LR = 8.74e-04
Epoch 14, Train loss = 0.1322, Accuracy: 0.9608, LR = 8.65e-04
Epoch 15, Train loss = 0.1348, Accuracy: 0.9609, LR = 8

### Visualising model

In [ ]:
show(model, batch_idx=0, mode="easy")

Average cross entropy loss: 0.120
Mean probability on correct label: 0.947
Median probability on correct label: 0.998
Min probability on correct label: 0.000


# Transformer (medium)

### Demo of dataset in medium mode

In [ ]:
data = CodeBreakingDataset(mode="medium", size=5, word_list_size=100, seq_len=32, path="hitchhikers.txt")

table = Table("Pre-encoding", "Post-encoding", "Rotation", title="Easy mode")
for i in range(5):
    rotation = int(data.str_labels[i])
    rotation_explained = f"{rotation:02}: a -> {string.ascii_lowercase[rotation % 26]}, b -> {string.ascii_lowercase[(rotation + 1) % 26]}, ..."
    table.add_row(
        "".join(data.str_toks_raw[i]),
        "".join(data.str_toks[i]),
        rotation_explained,
    )
rprint(table)

                                            Easy mode                                            
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Pre-encoding                     ┃ Post-encoding                    ┃ Rotation                ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ ran say had mud ask let ten and  │ jsf ksq zsv emv skc dwl lwf sfv  │ 18: a -> s, b -> t, ... │
│ sea sun got ten his pub sit far  │ nzv npi bjo ozi cdn kpw ndo avm  │ 21: a -> v, b -> w, ... │
│ its job dry lie old red run end  │ ozy puh jxe rok urj xkj xat ktj  │ 06: a -> g, b -> h, ... │
│ off sun nor got she god now god  │ sjj wyr rsv ksx wli ksh rsa ksh  │ 04: a -> e, b -> f, ... │
│ cut her arm cup god our how air  │ gyx liv evq gyt ksh syv lsa emv  │ 04: a -> e, b -> f, ... │
└──────────────────────────────────┴──────────────────────────────────┴─────────────────────────┘

### Training model

In [ ]:
args = TrainArgs(

    # Training arguments
    trainset_size=150_000,
    valset_size=10_000,
    epochs=100,
    batch_size=512,
    lr_start=1e-3,
    lr_end=1e-4,
    weight_decay=0.001,
    seed=42,
    use_wandb=False,
    device=device,

    # Model architecture arguments
    d_model=48,
    d_head=24,
    n_layers=2,
    n_heads=2,
    d_mlp=None,
    normalization_type="LN",
    
    # Dataset arguments
    mode="medium",
    word_list_size=100,
    seq_len=32,
    path="hitchhikers.txt",
)

# Train the model
model = train(args)

# Save the model
filename = section_dir / "code_breaking_model_medium.pt"
t.save(model.state_dict(), filename)

Building dataset...:   0%|          | 0/150000 [00:00<?, ?it/s]

Epoch 00, Train loss = 0.6163, Accuracy: 0.8261, LR = 9.91e-04
Epoch 01, Train loss = 0.4846, Accuracy: 0.8573, LR = 9.82e-04
Epoch 02, Train loss = 0.4080, Accuracy: 0.8735, LR = 9.73e-04
Epoch 03, Train loss = 0.3742, Accuracy: 0.8851, LR = 9.64e-04
Epoch 04, Train loss = 0.3358, Accuracy: 0.8919, LR = 9.55e-04
Epoch 05, Train loss = 0.3169, Accuracy: 0.8974, LR = 9.46e-04
Epoch 06, Train loss = 0.3280, Accuracy: 0.9021, LR = 9.37e-04
Epoch 07, Train loss = 0.3153, Accuracy: 0.9060, LR = 9.28e-04
Epoch 08, Train loss = 0.2843, Accuracy: 0.9097, LR = 9.19e-04
Epoch 09, Train loss = 0.2929, Accuracy: 0.9113, LR = 9.10e-04
Epoch 10, Train loss = 0.2721, Accuracy: 0.9140, LR = 9.01e-04
Epoch 11, Train loss = 0.2718, Accuracy: 0.9168, LR = 8.92e-04
Epoch 12, Train loss = 0.2672, Accuracy: 0.9182, LR = 8.83e-04
Epoch 13, Train loss = 0.2584, Accuracy: 0.9189, LR = 8.74e-04
Epoch 14, Train loss = 0.2504, Accuracy: 0.9199, LR = 8.65e-04
Epoch 15, Train loss = 0.2473, Accuracy: 0.9215, LR = 8

### Visualising model

In [ ]:
show(model, batch_idx=0, mode="medium")

Average cross entropy loss: 0.206
Mean probability on correct label: 0.909
Median probability on correct label: 0.997
Min probability on correct label: 0.001


# Transformer (hard)

### Demo of dataset in hard mode

Note - the first time you run this, it might take a while to download the dataset. Subsequent runs will be faster, as the dataset will be cached locally.

In [ ]:
data = CodeBreakingDataset(mode="hard", size=5, seq_len=96)

table = Table("Pre-encoding", "Post-encoding", "Rotation", title="Easy mode", show_lines=True)
for i in range(5):
    rotation = int(data.str_labels[i])
    rotation_explained = f"{rotation:02}: a -> {string.ascii_lowercase[rotation % 26]}, b -> {string.ascii_lowercase[(rotation + 1) % 26]}, ..."
    table.add_row(
        repr("".join(data.str_toks_raw[i])),
        repr("".join(data.str_toks[i])),
        rotation_explained,
    )
rprint(table)

                                                     Easy mode                                                     
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Pre-encoding                              ┃ Post-encoding                             ┃ Rotation                ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ ' interpreted his sharp criticism of mr.  │ ' aflwjhjwlwv zak kzsjh ujalauake gx ej.  │ 18: a -> s, b -> t, ... │
│ obama as open support for mitt            │ gtses sk ghwf kmhhgjl xgj eall            │                         │
│ romney.\n\nadvertisement co'              │ jgefwq.\n\nsvnwjlakwewfl ug'              │                         │
├───────────────────────────────────────────┼───────────────────────────────────────────┼─────────────────────────┤
│ 'isputed returns in .\n\na spokesman for  │ 'dnkpozy mzopmin di .\n\nv nkjfznhvi ajm  │ 21: a -> v, b -> w, ... │
│ hanson told guardian australia that       │ cvinji ojgy bpvmydvi vpnomvgdv ocvo       │                         │
│ katter should "stay ou'                   │ fvoozm ncjpgy "novt jp'                   │                         │
├───────────────────────────────────────────┼───────────────────────────────────────────┼─────────────────────────┤
│ 'was an honor to be a part of the         │ 'cgy gt nutux zu hk g vgxz ul znk         │ 06: a -> g, b -> h, ... │
│ festival program this year."\n\nalex      │ lkyzobgr vxumxgs znoy ekgx."\n\ngrkd      │                         │
│ winter, director, deep web\n\n'           │ cotzkx, joxkizux, jkkv ckh\n\n'           │                         │
├───────────────────────────────────────────┼───────────────────────────────────────────┼─────────────────────────┤
│ 'ed as a way for locals and visitors to   │ 'ih ew e aec jsv psgepw erh zmwmxsvw xs   │ 04: a -> e, b -> f, ... │
│ experience the tranquillity of the        │ ibtivmirgi xli xveruymppmxc sj xli        │                         │
│ rainforest without lea'                   │ vemrjsviwx amxlsyx pie'                   │                         │
├───────────────────────────────────────────┼───────────────────────────────────────────┼─────────────────────────┤
│ 'extra features found in higherpriced     │ 'ibxve jiexyviw jsyrh mr lmklivtvmgih     │ 04: a -> e, b -> f, ... │
│ versions. separating its trucks into a    │ zivwmsrw. witevexmrk mxw xvygow mrxs e    │                         │
│ new nameplate, ram, '                     │ ria reqitpexi, veq, '                     │                         │
└───────────────────────────────────────────┴───────────────────────────────────────────┴─────────────────────────┘

### Training model

In [ ]:
args = TrainArgs(

    # Training arguments
    trainset_size=150_000,
    valset_size=10_000,
    epochs=100,
    batch_size=512,
    lr_start=1e-3,
    lr_end=1e-4,
    weight_decay=0.001,
    seed=42,
    use_wandb=False,
    device=device,

    # Model architecture arguments
    d_model=48,
    d_head=24,
    n_layers=2,
    n_heads=2,
    d_mlp=None,
    normalization_type="LN",
    
    # Dataset arguments
    mode="hard",
    seq_len=32,
)

# Train the model
model = train(args)

# Save the model
filename = section_dir / "code_breaking_model_hard.pt"
t.save(model.state_dict(), filename)

Running `get_webtext`...
Finished running `get_webtext`.


Processing data...:   0%|          | 0/150000 [00:00<?, ?it/s]

Epoch 00, Train loss = 0.9240, Accuracy: 0.7380, LR = 9.91e-04
Epoch 01, Train loss = 0.7742, Accuracy: 0.7607, LR = 9.82e-04
Epoch 02, Train loss = 0.7553, Accuracy: 0.7744, LR = 9.73e-04
Epoch 03, Train loss = 0.6755, Accuracy: 0.7833, LR = 9.64e-04
Epoch 04, Train loss = 0.6835, Accuracy: 0.7945, LR = 9.55e-04
Epoch 05, Train loss = 0.6551, Accuracy: 0.8030, LR = 9.46e-04
Epoch 06, Train loss = 0.6641, Accuracy: 0.8103, LR = 9.37e-04
Epoch 07, Train loss = 0.6160, Accuracy: 0.8147, LR = 9.28e-04
Epoch 08, Train loss = 0.6164, Accuracy: 0.8204, LR = 9.19e-04
Epoch 09, Train loss = 0.5783, Accuracy: 0.8223, LR = 9.10e-04
Epoch 10, Train loss = 0.5880, Accuracy: 0.8256, LR = 9.01e-04
Epoch 11, Train loss = 0.5657, Accuracy: 0.8260, LR = 8.92e-04
Epoch 12, Train loss = 0.5823, Accuracy: 0.8278, LR = 8.83e-04
Epoch 13, Train loss = 0.5558, Accuracy: 0.8283, LR = 8.74e-04
Epoch 14, Train loss = 0.5701, Accuracy: 0.8310, LR = 8.65e-04
Epoch 15, Train loss = 0.5736, Accuracy: 0.8313, LR = 8

### Visualising model

In [ ]:
show(model, batch_idx=0, mode="hard")

Average cross entropy loss: 0.477
Mean probability on correct label: 0.801
Median probability on correct label: 0.984
Min probability on correct label: 0.000
